In [17]:
import pandas as pd
pd.options.display.float_format = '{:,.4f}'.format
pd.options.display.max_rows = 100
pd.options.display.max_columns = 40
import numpy as np
import os,random, math
from tqdm import tqdm
from copy import deepcopy
from collections import Counter

# Visualization
import seaborn as sns
import matplotlib
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib import font_manager, rc
plt.rcParams['font.family'] = 'NanumGothic'
import platform
if platform.system() == 'Windows':
    font_name = font_manager.FontProperties(fname="c:/Windows/Fonts/malgun.ttf").get_name()
    rc('font', family=font_name)
else:    
    rc('font', family='AppleGothic')

matplotlib.rcParams['axes.unicode_minus'] = False

# from dataprep.eda import plot, plot_correlation, plot_missing

import plotly 
import plotly.express as px
# from plotly import tools, subplots
# import plotly.offline as py
# py.init_notebook_mode(connected=True)
# from plotly.offline import init_notebook_mode, iplot
# import plotly.graph_objs as go
# import plotly.express as px

# Warnings
import warnings
warnings.filterwarnings('always')
warnings.filterwarnings('ignore')
# row 생략 없이 출력
# pd.set_option('display.max_rows', None)
# col 생략 없이 출력
pd.set_option('display.max_columns', None)
from sklearn.metrics import mean_absolute_error

In [3]:
rawtest = pd.read_csv("/Users/seungji/Desktop/Dacon/Daesamanlap/ProcessedData/merged_test.csv")
rawtrain = pd.read_csv("/Users/seungji/Desktop/Dacon/Daesamanlap/ProcessedData/merged_train.csv")

In [4]:
test = pd.read_csv("/Users/seungji/Desktop/Dacon/Daesamanlap/ProcessedData/merged_test.csv")
train = pd.read_csv("/Users/seungji/Desktop/Dacon/Daesamanlap/ProcessedData/merged_train.csv")

In [5]:
# merged_ data에서 drop해야 할 단지코드
print(train.shape, test.shape)
train = train.loc[~train.단지코드.isin(['C1095', 'C2051', 'C1218', 'C1894', 'C2483', 'C1502', 'C1988']),]
test = test.loc[~test.단지코드.isin(['C2335', 'C1327', 'C2675'])]
print(train.shape, test.shape)

(2896, 34) (1008, 33)
(2896, 34) (1008, 33)


In [6]:
train.at[range(1481,1487),"총세대수"]=969
train.at[range(1624,1632),"총세대수"]=969
train.at[range(1481,1487),"공가수"]=9
train.at[range(1624,1632),"공가수"]=9

train.at[range(1753,1757),"총세대수"]=1047
train.at[range(1810,1812),"총세대수"]=1047
train.at[range(1753,1757),"공가수"]=31
train.at[range(1810,1812),"공가수"]=31
train.at[range(1753,1757),"등록차량수"]=1214
train.at[range(1810,1812),"등록차량수"]=1214
train.at[range(1753,1757),"버스정류장"]=4
train.at[range(1810,1812),"버스정류장"]=4

In [7]:
train=train.drop_duplicates(keep='first')
test=test.drop_duplicates(keep='first')

In [8]:
print("\n...Before preprocessing")
print(train.shape, test.shape)

# 상가비율 column 추가
train_cls = pd.concat([train[['단지코드']], pd.get_dummies(train[['임대건물구분']])], axis=1).groupby('단지코드').sum()
tot = train_cls['임대건물구분_상가']+train_cls['임대건물구분_아파트']
train_cls['상가비율'] = train_cls['임대건물구분_상가']/tot
train = pd.merge(train,train_cls[['상가비율']].reset_index(),on='단지코드')

test_cls = pd.concat([test[['단지코드']], pd.get_dummies(test[['임대건물구분']])], axis=1).groupby('단지코드').sum()
tot = test_cls['임대건물구분_상가']+test_cls['임대건물구분_아파트']
test_cls['상가비율'] = test_cls['임대건물구분_상가']/tot
test = pd.merge(test,test_cls[['상가비율']].reset_index(),on='단지코드')

# 세대당_가능주차면수 column 추기
train['세대당_가능주차면수'] = train['단지내주차면수']/train['총세대수']
test['세대당_가능주차면수'] = test['단지내주차면수']/test['총세대수']

# 공가수비율 column 추가
train['공가수비율']= train.공가수/train.총세대수 
test['공가수비율']= test.공가수/test.총세대수 

# 대형전용면적 column 추가
level = 85
train['대형전용면적'] = 0
train.loc[train.전용면적>level, '대형전용면적'] = 1
train.loc[train.전용면적<=level, '대형전용면적'] = 0

test['대형전용면적'] = 0
test.loc[test.전용면적>level, '대형전용면적'] = 1
test.loc[test.전용면적<=level, '대형전용면적'] = 0

# check
print("\n...After preprocessing")
print(train.shape, test.shape)


...Before preprocessing
(2577, 34) (936, 33)

...After preprocessing
(2577, 38) (936, 37)


In [9]:
dic = {'1': 'A' ,'2':['C','F','G'],'3':['B','H','I'],'4':['J'],
       '5':['L',"M","N","O"],'6':["E","K"],'7':'D'}

In [10]:
def mapping_by_key(dic, x):
    for i in dic.keys():
        if x in dic[i]:
            return int(i)

In [11]:
train['자격유형_카테고리'] = train['자격유형'].apply(lambda x : mapping_by_key(dic, x))
train['자격유형_카테고리'] = train['자격유형_카테고리'].astype(object)
test['자격유형_카테고리'] = test['자격유형'].apply(lambda x : mapping_by_key(dic, x))
test['자격유형_카테고리'] = test['자격유형_카테고리'].astype(object)
train= train.drop(columns="자격유형")
test= test.drop(columns="자격유형")

In [12]:
train.shape

(2577, 38)

## 공급유형

In [13]:
train.loc[train.공급유형.isin(['공공임대(5년)', '공공임대(10년)']), '공급유형'] = '공공임대(단기)'
test.loc[test.공급유형.isin(['공공임대(5년)', '공공임대(10년)']), '공급유형'] = '공공임대(단기)'

In [15]:
print(train.shape)
print(test.shape)


(2577, 38)
(936, 37)


In [16]:
train

단지코드  총세대수 임대건물구분       지역       공급유형     전용면적  전용면적별세대수     공가수  \
0     C2515   545    아파트     경상남도       국민임대  33.4800       276 17.0000   
1     C2515   545    아파트     경상남도       국민임대  39.6000        60 17.0000   
2     C2515   545    아파트     경상남도       국민임대  39.6000        20 17.0000   
3     C2515   545    아파트     경상남도       국민임대  46.9000        38 17.0000   
4     C2515   545    아파트     경상남도       국민임대  46.9000        19 17.0000   
5     C2515   545    아파트     경상남도       국민임대  51.9700       106 17.0000   
6     C2515   545    아파트     경상남도       국민임대  51.9700        26 17.0000   
7     C1407  1216    아파트    대전광역시       국민임대  30.9500       288 13.0000   
8     C1407  1216    아파트    대전광역시       국민임대  30.9900        68 13.0000   
9     C1407  1216    아파트    대전광역시       국민임대  30.9900        34 13.0000   
10    C1407  1216    아파트    대전광역시       국민임대  41.1100       148 13.0000   
11    C1407  1216    아파트    대전광역시       국민임대  41.3900        74 13.0000   
12    C1407  1216    아파트    대전광역시       국민임대  41.5800        70 13.0000   
13    C1407  1216    아파트    대전광역시       국민임대  46.3600       170 13.0000   
14    C1407  1216    아파트    대전광역시       국민임대  51.2400        62 13.0000   
15    C1945   755    아파트      경기도       국민임대  39.7200       120  6.0000   
16    C1945   755    아파트      경기도       국민임대  51.9300       207  6.0000   
17    C1945   755    아파트      경기도       국민임대  51.9300        96  6.0000   
18    C1945   755    아파트      경기도       국민임대  59.8800       160  6.0000   
19    C1945   755    아파트      경기도       국민임대  59.8800        52  6.0000   
20    C1470   696    아파트     전라북도       국민임대  36.5500       228 14.0000   
21    C1470   696    아파트     전라북도       국민임대  36.5500        26 14.0000   
22    C1470   696    아파트     전라북도       국민임대  46.9000       196 14.0000   
23    C1470   696    아파트     전라북도       국민임대  51.9300       246 14.0000   
24    C1898   566    아파트     전라북도       국민임대  36.5500       230  9.0000   
25    C1898   566    아파트     전라북도       국민임대  36.5500        28  9.0000   
26    C1898   566    아파트     전라북도       국민임대  36.6200        13  9.0000   
27    C1898   566    아파트     전라북도       국민임대  46.9000       194  9.0000   
28    C1898   566    아파트     전라북도       국민임대  46.9000        15  9.0000   
29    C1898   566    아파트     전라북도       국민임대  51.9300        86  9.0000   
30    C1244  1722    아파트      경기도       국민임대  39.6200       275 10.0000   
31    C1244  1722    아파트      경기도       국민임대  39.6200       126 10.0000   
32    C1244  1722    아파트      경기도       국민임대  39.6200       168 10.0000   
33    C1244  1722    아파트      경기도       국민임대  39.7200       219 10.0000   
34    C1244  1722    아파트      경기도       국민임대  46.7300        98 10.0000   
35    C1244  1722    아파트      경기도       국민임대  46.8100       144 10.0000   
36    C1244  1722    아파트      경기도       국민임대  46.8100        76 10.0000   
37    C1244  1722    아파트      경기도       국민임대  46.9500        75 10.0000   
38    C1244  1722    아파트      경기도       국민임대  51.7800       232 10.0000   
39    C1244  1722    아파트      경기도       국민임대  51.7800        83 10.0000   
40    C1244  1722    아파트      경기도       국민임대  51.9500        75 10.0000   
41    C1171   624    아파트    대전광역시       국민임대  33.3800       190 13.0000   
42    C1171   624    아파트    대전광역시       국민임대  39.4600       106 13.0000   
43    C1171   624    아파트    대전광역시       국민임대  39.4600        43 13.0000   
44    C1171   624    아파트    대전광역시       국민임대  39.4600        15 13.0000   
45    C1171   624    아파트    대전광역시       국민임대  46.6600        38 13.0000   
46    C1171   624    아파트    대전광역시       국민임대  46.6600        15 13.0000   
47    C1171   624    아파트    대전광역시       국민임대  46.8700        46 13.0000   
48    C1171   624    아파트    대전광역시       국민임대  46.8700        23 13.0000   
49    C1171   624    아파트    대전광역시       국민임대  46.8800        78 13.0000   
50    C1171   624    아파트    대전광역시       국민임대  46.8800        30 13.0000   
51    C1171   624    아파트    대전광역시       국민임대  51.9600        20 13.0000   
52    C2073   361    아파트      강원

In [ ]:
data = train.drop(columns=['공급유형','자격유형_카테고리','전용면적','임대건물구분',
                           '전용면적별세대수','대형전용면적','자격유형_카테고리',
                           '임대보증금','임대료'])
data = data.drop_duplicates()

In [ ]:
data.shape

## 1차원

### train

In [ ]:
sample = pd.DataFrame(train.groupby(['단지코드','공급유형']).mean()['전용면적별세대수']).reset_index()

## 은영이랑 달라지는 부분

### 전용면적, 전용면적별세대수 

In [ ]:
tr_gr = tr.merge(rawtrain.groupby("단지코드").mean().reset_index()[["단지코드","전용면적",'전용면적별세대수','임대료',"임대보증금"]], left_on = "단지코드",right_on= "단지코드", how = "left")
tst_gr = tst.merge(rawtest.groupby("단지코드").mean().reset_index()[["단지코드","전용면적",'전용면적별세대수','임대료',"임대보증금"]], left_on = "단지코드",right_on= "단지코드", how = "left")

### 전용면적, 전용면적별세대수 std

In [ ]:
tr_gr["전용면적_std"] = rawtrain.groupby("단지코드").std().reset_index()["전용면적"]
tr_gr["전용면적별세대수_std"] = rawtrain.groupby("단지코드").std().reset_index()["전용면적별세대수"]
tr_gr["임대보증금_std"] = rawtrain.groupby("단지코드").std().reset_index()["임대보증금"]
tr_gr["임대료_std"] = rawtrain.groupby("단지코드").std().reset_index()["임대료"]

tst_gr["전용면적_std"] = rawtest.groupby("단지코드").std().reset_index()["전용면적"]
tst_gr["전용면적별세대수_std"] = rawtest.groupby("단지코드").std().reset_index()["전용면적별세대수"]
tst_gr["임대보증금_std"] = rawtest.groupby("단지코드").std().reset_index()["임대보증금"]
tst_gr["임대료_std"] = rawtest.groupby("단지코드").std().reset_index()["임대료"]

tr_gr.loc[tr_gr.전용면적_std.isna(),"전용면적_std"] = 0
tr_gr.loc[tr_gr.전용면적별세대수_std.isna(),"전용면적별세대수_std"] = 0
tr_gr.loc[tr_gr.임대보증금_std.isna(),"임대보증금_std"] = 0
tr_gr.loc[tr_gr.임대료_std.isna(),"임대료_std"] = 0